In [2]:
import pandas as pd
import numpy as np
from sklearn import tree, preprocessing, impute
from sklearn.model_selection import train_test_split
from sklearn.tree import export_graphviz
import graphviz
from sklearn.model_selection import cross_val_score, GridSearchCV

df = pd.read_csv("final_data_removed_lowcounts.csv")
del df['Unnamed: 0']
del df['movieId']
df

count  avg_rating            director      genre  year  \
0      49695.0    3.921240       John Lasseter  Animation  1995   
1      22243.0    3.211977        Joe Johnston  Adventure  1995   
2      12735.0    3.151040       Howard Deutch     Comedy  1995   
3       2756.0    2.861393     Forest Whitaker     Comedy  1995   
4      12161.0    3.064592       Charles Shyer     Comedy  1995   
...        ...         ...                 ...        ...   ...   
17225     12.0    2.666667  Jaume Collet-Serra     Action  2015   
17226     21.0    3.404762     Kenneth Branagh      Drama  2015   
17227     17.0    2.500000          Chris Buck  Animation  2015   
17228     25.0    3.240000    Robert Schwentke     Action  2015   
17229      7.0    2.714286    Jalmari Helander     Action  2014   

               LeadActor language  
0              Tom Hanks  English  
1         Robin Williams  English  
2         Walter Matthau  English  
3        Whitney Houston  English  
4           Steve Martin  English  
...                  ...      ...  
17225        Liam Neeson  English  
17226     Cate Blanchett  English  
17227       Kristen Bell  English  
17228       Kate Winslet  English  
17229  Samuel L. Jackson  English  

[17230 rows x 7 columns]

# WHAT MUST BE DONE:
1) create X (all data except movieId and rating) and Y (rating only) dataframes <br>
2) encode X data (specifically director, LeadActor, genre, language) <br>
3) encode Y data, map to make binary (e.g. rating < 3.0 means 'bad (0)' and above means 'good (1)') <br>
4) split into testing and training <br>
5) fit decision tree to create models and make predictions, check accuracy <br>
6) check accuracy or whatever

In [3]:
#Can't do pd.get_dummies because the dataframe is too large --> maybe can with removed_lowcounts csv
X = df.copy()
del X['avg_rating']
#del X['count'] <--> NOT deleting because amount of times movies are rated has significance

X = pd.get_dummies(X, columns=['year','director','genre','LeadActor','language'])
X

count  year_1894  year_1902  year_1903  year_1910  year_1914  \
0      49695.0          0          0          0          0          0   
1      22243.0          0          0          0          0          0   
2      12735.0          0          0          0          0          0   
3       2756.0          0          0          0          0          0   
4      12161.0          0          0          0          0          0   
...        ...        ...        ...        ...        ...        ...   
17225     12.0          0          0          0          0          0   
17226     21.0          0          0          0          0          0   
17227     17.0          0          0          0          0          0   
17228     25.0          0          0          0          0          0   
17229      7.0          0          0          0          0          0   

       year_1915  year_1916  year_1917  year_1918  ...  language_Tibetan  \
0              0          0          0          0  ...                 0   
1              0          0          0          0  ...                 0   
2              0          0          0          0  ...                 0   
3              0          0          0          0  ...                 0   
4              0          0          0          0  ...                 0   
...          ...        ...        ...        ...  ...               ...   
17225          0          0          0          0  ...                 0   
17226          0          0          0          0  ...                 0   
17227          0          0          0          0  ...                 0   
17228          0          0          0          0  ...                 0   
17229          0          0          0          0  ...                 0   

       language_Tswana  language_Turkish  language_Ukrainian  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   
...                ...               ...                 ...   
17225                0                 0                   0   
17226                0                 0                   0   
17227                0                 0                   0   
17228                0                 0                   0   
17229                0                 0                   0   

       language_Ukrainian Sign Language  language_Urdu  language_Vietnamese  \
0                                     0              0                    0   
1                                     0              0                    0   
2                                     0              0                    0   
3                                     0              0                    0   
4                                     0              0                    0   
...                                 ...            ...                  ...   
17225                                 0              0                    0   
17226                                 0              0                    0   
17227                                 0              0                    0   
17228                                 0              0                    0   
17229                                 0              0                    0   

       language_Welsh  language_Wolof  language_Zulu  
0                   0               0              0  
1                   0               0              0  
2                   0               0              0  
3                   0               0              0  
4                   0               0              0  
...               ...             ...            ...  
17225               0               0              0  
17226               0               0              0  
17227 

In [4]:
Y = df[['avg_rating']].copy()

#mapping ratings to create binary conditions for classifier
for i in range(0, len(Y)):
    if Y.loc[i, 'avg_rating'] < 3.5:
        Y.loc[i, 'avg_rating'] = 0
    else:
        Y.loc[i, 'avg_rating'] = 1

Y

avg_rating
0             1.0
1             0.0
2             0.0
3             0.0
4             0.0
...           ...
17225         0.0
17226         0.0
17227         0.0
17228         0.0
17229         0.0

[17230 rows x 1 columns]

In [5]:
x_train, x_test, y_train, y_test = train_test_split(X, Y, test_size=0.3, random_state=35)

In [11]:
from IPython.display import Image
from subprocess import call

dtc = tree.DecisionTreeClassifier(random_state=35)
dtc.fit(x_train, y_train)

"""
I THINK THE TREE MIGHT BE TOO LARGE AND THE PROGRAM TO CONVERT TO .PNG IS FAILING
tree.export_graphviz(dtc, out_file='tree.dot', feature_names=x_train.columns)

#run the graphviz exectable to alter the .dot to .png
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png'], shell=True)
Image(filename = 'tree.png') #view the image
"""

tree_params = {'criterion':['gini','entropy'],'max_leaf_nodes':[None,3,6,9],'max_depth':[None,5,10,20,30,50]}
gscv = GridSearchCV(tree.DecisionTreeClassifier(), tree_params, cv=5)
gscv.fit(x_train, y_train)
print(gscv.best_params_)

{'criterion': 'gini', 'max_depth': 20, 'max_leaf_nodes': None}


In [13]:
new_dtc = tree.DecisionTreeClassifier(criterion=gscv.best_params_.get('criterion'),
                                      max_leaf_nodes=gscv.best_params_.get('max_leaf_nodes'),
                                      max_depth=gscv.best_params_.get('max_depth'),
                                      random_state=35)
#tree.DecisionTreeRegressor()
new_dtc.fit(x_train, y_train)
tree.export_graphviz(new_dtc, out_file='tree2.dot', feature_names=x_train.columns)

#run the graphviz exectable to alter the .dot to .png
call(['dot', '-Tpng', 'tree2.dot', '-o', 'tree2.png'], shell=True)
Image(filename = 'tree2.png') #view the image

In [19]:
from sklearn.metrics import accuracy_score

y_pred = dtc.predict(x_test)
y_test_vals = y_test['avg_rating'].values
print(accuracy_score(y_test_vals, y_pred))

0.738634165215709


## WOW, pretty good accuracy tbh